<a href="https://colab.research.google.com/github/TerranceRandolph/Data-Analysis/blob/master/IST_652_HW1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

<h1>Terrance Randolph  |  IST 654  |  Homework 1</h1>

---

> <h4>--The data captures the reactions consumers have from food, medical and other products to the Food and Drug Administration.</h4>
> <h4>--Those reactions are recorded by datetime and final symptom reaction from the product such as rash or more saver reactions such as a comma or death.</h4> 
> <h4>--Therefore, this dataset allows the data scientist to understand what ages are most at risk when using certain products and what products causes the most problems.</h4>

---

> FDA for foods, dietary supplements, and cosmetics. The database is designed to support CFSAN's safety surveillance program.


---

> The original dataset can be downloaded from [Kaggle's Website](https://www.kaggle.com/fda/adverse-food-events). The site downloads a zipfile contains a READ ME file that can also be found on the [FDA website](https://www.fda.gov/media/97035/download)



 
*   Columns: 11
*   Rows: 90786  × 11


In [0]:
import os
import pandas as pd  # data frame operations
import numpy as np  # arrays and math functions
import plotly.express as px # interactive graphing lib.
import plotly.graph_objects as go

<h1> Data Reading </h1>


In [13]:
# ----------------------------------------
# read CSV's into pandas
care = pd.read_csv('/content/drive/My Drive/Village 3A/Big Data/Scripting for data/CAERS_ASCII_2004_2017Q2.csv')
#
dfCare = pd.DataFrame(care)
dfCare.columns # 11 columns in total 
# ----------------------------------------

Index(['RA_Report #', 'RA_CAERS Created Date', 'AEC_Event Start Date',
       'PRI_Product Role', 'PRI_Reported Brand/Product Name',
       'PRI_FDA Industry Code', 'PRI_FDA Industry Name',
       'CI_Age at Adverse Event', 'CI_Age Unit', 'CI_Gender',
       'AEC_One Row Outcomes', 'SYM_One Row Coded Symptoms'],
      dtype='object')

In [0]:
# ----------------------------------------
# extract columns needed from the 11
dfCare = dfCare[['RA_CAERS Created Date', 'PRI_FDA Industry Name',
                 'CI_Age at Adverse Event', 'CI_Gender', 'SYM_One Row Coded Symptoms']]
# rename the 5 columns that were extracted
dfCare.columns = ['Created_Date','Product_Cat',
                 'Reporter_Age', 'Reporter_Gender', 'Symptom_Outcome']
# ----------------------------------------

In [15]:
# print head of data
dfCare.head()

Created_Date  ...                                    Symptom_Outcome
0     1/1/2004  ...  SWELLING FACE, RASH, WHEEZING, COUGH, HOSPITAL...
1     1/1/2004  ...  SWELLING FACE, WHEEZING, COUGH, RASH, HOSPITAL...
2     1/1/2004  ...                       NAUSEA, DYSGEUSIA, DIARRHOEA
3     1/1/2004  ...                GASTROINTESTINAL DISORDER, VOMITING
4     1/1/2004  ...    GASTROINTESTINAL DISORDER, PHYSICAL EXAMINATION

[5 rows x 5 columns]

# Data Cleaning

In [16]:
# ----------------------------------------
# if gender is null remove
dfCare = dfCare[dfCare['Reporter_Gender'].notnull()]
# replace any not available with UNK
dfCare = dfCare.replace('Not Available','UNK').replace(np.nan, 0) 
# ----------------------------------------
# change column to type integer
dfCare['Reporter_Age'] = dfCare['Reporter_Age'].astype(int)
# converte column to datetime
dfCare['Created_Date'] = pd.to_datetime(dfCare['Created_Date'])
# create month column from datetime structure
dfCare['Created_Month'] = pd.DatetimeIndex(dfCare['Created_Date']).month
# create year column from datetime structure
dfCare['Created_Year'] = pd.DatetimeIndex(dfCare['Created_Date']).year
# drop the column "created_Date" from dataframe
dfCare.drop(['Created_Date'],axis = 1, inplace=True)
# ----------------------------------------
# replace ',' & '/' by looping through list
dfCare.Symptom_Outcome = [str(symp).split(',')[0] for symp in dfCare['Symptom_Outcome']]
dfCare.Product_Cat = [str(prod).split('/')[0] for prod in dfCare['Product_Cat']]
# filter from 2007 - 2017 where data ends, since data set dates multiple decades
Care = dfCare[dfCare['Created_Year'] >= 2007]
# ----------------------------------------
# establish ranges for age groups 
bins = [0, 18, 30, 50, 75, 100] # 'youth','young_adult','adult', 'middle_age','elderly'
# create columns with age ranges for better viz's
Care['Ages_binned'] = pd.cut(Care['Reporter_Age'], bins, 
                             labels= ['youth','young_adult',
                                      'adult', 'middle_age','elderly'])
# drop any N/A in rows from this column
Care = Care.dropna(subset=['Ages_binned']) ; Care['Ages_binned']


/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:26: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



8033         elderly
8034     young_adult
8035           adult
8036      middle_age
8037      middle_age
            ...     
90779          youth
90780          youth
90781     middle_age
90782     middle_age
90783     middle_age
Name: Ages_binned, Length: 49723, dtype: category
Categories (5, object): [youth < young_adult < adult < middle_age < elderly]

In [0]:
# ----------------------------------------
# get occorance of symptom's in dataset
sym = Care.Symptom_Outcome.value_counts()
# convert to dictionary for easy maping
sym1 = sym.to_dict() 
# create a new column with occorance information
Care['Count_Symptoms'] = Care['Symptom_Outcome'].map(sym1)
# ----------------------------------------
prod = Care.Product_Cat.value_counts()
prod1 = prod.to_dict() #converts to dictionary
Care['Count_Product'] = Care['Product_Cat'].map(prod1)
# ----------------------------------------

In [18]:
Care.head()

Product_Cat  Reporter_Age  ... Count_Symptoms Count_Product
8033          Vit            81  ...             33         34550
8034          Vit            27  ...            243         34550
8035          Vit            35  ...            128         34550
8036          Vit            68  ...           2508         34550
8037  Bakery Prod            73  ...           2272           755

[5 rows x 9 columns]

In [19]:
Care_Stats = Care.describe() ; Care_Stats

Reporter_Age  Created_Month  Created_Year  Count_Symptoms  Count_Product
count  49723.000000   49723.000000  49723.000000    49723.000000   49723.000000
mean      51.343061       6.389920   2013.167448      725.139533   24591.096454
std       22.374107       3.380524      2.664725      807.865918   15063.419127
min        1.000000       1.000000   2007.000000        1.000000       8.000000
25%       35.000000       3.000000   2011.000000       74.000000    4675.000000
50%       54.000000       6.000000   2014.000000      341.000000   34550.000000
75%       69.000000       9.000000   2015.000000     1178.000000   34550.000000
max      100.000000      12.000000   2017.000000     2508.000000   34550.000000

<h3>Export basic statistics to csv</h3>

In [0]:
# export 
# Care_Stats.to_csv('/content/drive/My Drive/Village 3A/Big Data/Scripting for data/Care_Data_Stats.csv')

<h1>Question2: What is the spread of the columns in the dataset?</h1>

<h3>Large swings are not evident in consumer reactions based on month, although August has the highest one cannot assume seasonality in this dataset.</h3>

In [21]:
fig = px.histogram(Care, x= 'Created_Month')
fig.show()


<h3>From years 2007 - 2017 there is a gradual increase with a sharp spike in 2016 but 2017 indicats a sharpe drop. Therefore, more investigations is needed to understand the disparities from 2016 to 2017.</h3>

In [22]:
fig = px.histogram(Care, x='Created_Year')
fig.show()

<h3>Top/most common symptoms from products are Choking, Vomiting, Diarrhoea and Nausea.</h3>

In [23]:
fig = px.histogram(Care, x='Symptom_Outcome')
fig.show()

<h3>This heat map indicates that most product categories occur often and the symptoms from the previous chart seems to explain correspond popular products. However, Vitamins over the years have increasingly caused consumers to report them to the FDA with a huge spike in 2016. </h3>

In [24]:
fig = px.density_heatmap(Care, x="Created_Year", y="Product_Cat")
fig.show()

<h3>Excluding the unknown data, women seem to report their symptoms more frequently than men</h3>

In [25]:
fig = px.density_heatmap(Care, x="Created_Year", y="Reporter_Gender")
fig.show()

<h3>Those who are adults and middle aged adults tend to be more effected by these products more so then other age groups.</h3>

In [26]:
fig = px.density_heatmap(Care, x= 'Created_Year', y="Ages_binned")
fig.show()

<h1>Question1: 
What age groups had the most complaints and what were their most common symptoms and product category problem?</h1>

<h3>Top 3 product Categories that causes the majority of symptoms reported are ( Vitamins, Cosmetics and Dietary Supplements ) </h3>

In [28]:
fig = px.scatter(Care, x='Product_Cat', y='Symptom_Outcome')
fig.show()

<h3>Now that we know the most common product categories and what age groups are most likely effected or prone to reporting symptoms. This chart conveys that the middle-aged groups struggle the most with the established top products of Vitamins, Cosmetics and Dietary products.</h3>

In [31]:
fig = px.histogram(Care, x = "Product_Cat", y = 'Count_Product', color="Ages_binned",
                   hover_data=Care.columns)
fig.show()

<h3>Moreover, the most common symptoms seem to correspond to the common symptoms established before, however, Alopecia is a very common symptom for average and middle aged adults.</h3>

In [32]:
fig = px.histogram(Care, x = "Symptom_Outcome", y = 'Count_Symptoms', color="Ages_binned",
                   hover_data=Care.columns)
fig.show()